# Quantum Circuit Design through Monte Carlo Tree Search
In this tutorial we are going show the whole pipeline of the Monte Carlo Tree Search (MCTS) implemented for Quantum circuit Design.

## Problem Definition
First of all we need to assign a goal to the algorithm, namely we need to define an objective function to optimize. The objective function is a real-valued function defined on the domain of quantum circuits. In [`evaluation_functions.py`](./evaluation_functions.py), you can find examplesin the field of quantum chemistry, systems of linear equations, combinatorial optimization, and on quantum oracle approximation (a dataset of random quantum circuit that you want to approximate with repsect to the fidelity).  

As an example, let's consider the problem of finding the ground-state energy of a molecule using the Variational Quantum Eigensolver (VQE). For simplicity, we take the hydrogen molecule molecule $H_2$ as our test case. In the following, we create a random quantum circuit and then evaluate it as a solution for the ground state problem of the hydrogen.

In [22]:
from qiskit import QuantumCircuit
import evaluation_functions as evf

# Create a random quantum circuit
qc = QuantumCircuit(4)
for i in range(4):
    qc.ry(0.5, i)

# Define problem: you can select evf.h2, evf.h2o, evf.lih, evf.vqls_1, evf.vqls_0, etc ...
problem = evf.h2
cost_value = problem(qc, cost=True)

print(f"Given the quantum circuit below: \n{qc}\n the objective function returns: {cost_value}")

Given the quantum circuit below: 
     ┌─────────┐
q_0: ┤ Ry(0.5) ├
     ├─────────┤
q_1: ┤ Ry(0.5) ├
     ├─────────┤
q_2: ┤ Ry(0.5) ├
     ├─────────┤
q_3: ┤ Ry(0.5) ├
     └─────────┘
 the objective function returns: 0.5585648835784065


## Ansatz Search
Once we have defined the problem, we can use MCTS in order to design a suitable guess for the initial quantum circuit solving the problem. Then,  we will use a classical optimizer in order to fine-tune the parameters of the circuit.
First we need to fix the hyperparameters of the model. See below:

In [23]:
variable_qubits = 4
ancilla_qubits = 0
max_depth = 20
budget = 1000
branches = False
criteria = "value"
rollout_type = 'classic'
roll_out_steps = 0
choices = {'a': 50, 'd': 10, 's': 20, 'c': 20, 'p': 0}
epsilon = None
sim = False
stop_deterministic = False
ucb = 0.4
pw_C = 1
pw_alpha = 0.3


Then, we can define the root node with the initial quantum circuit. The search starts from that node and finally it outputs the best path starting from the root to the leaf that creates the best circuit

In [24]:
import mcts
from structure import Circuit
root = mcts.Node(Circuit(variable_qubits=variable_qubits, ancilla_qubits=ancilla_qubits), max_depth=max_depth)
        
best_path = mcts.mcts(root, budget=budget, branches=branches, evaluation_function=problem, criteria=criteria, rollout_type=rollout_type, roll_out_steps=roll_out_steps,
                                choices=choices, epsilon=epsilon, simulation=sim, stop_deterministic=stop_deterministic, ucb_value=ucb, pw_C=pw_C, pw_alpha=pw_alpha, verbose=True)

Root Node:
 Tree depth: 0  -  Generated by Action: None  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐
v_0: ┤ H ├
     ├───┤
v_1: ┤ H ├
     ├───┤
v_2: ┤ H ├
     ├───┤
v_3: ┤ H ├
     └───┘
Epoch Counter:  0
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐┌─────────────┐
v_0: ┤ H ├┤ Ry(0.69913) ├
     ├───┤└─────────────┘
v_1: ┤ H ├───────────────
     ├───┤               
v_2: ┤ H ├───────────────
     ├───┤               
v_3: ┤ H ├───────────────
     └───┘               
Reward:  0.1564470561095942
Epoch Counter:  1
Node Expanded:
 Tree depth: 1  -  Generated by Action: a  -  Number of Children: 0  -  Visits: 0  -  Value: 0  -  Quantum Circuit (CNOT counts)= 0):
     ┌───┐              
v_0: ┤ H ├──────────────
     ├───┤              
v_1: ┤ H ├──────────────
     ├───┤┌────────────┐
v_2: ┤ H ├┤ Rz(2.2947) ├
     ├─

In the following we print the values of the objective function of the quantum circuits designed along the path

In [25]:
quantum_circuit_path = best_path['qc']
cost = []
for i in range(len(quantum_circuit_path)):
    cost.append(problem(quantum_circuit_path[i], cost=True))
    print("Node at depth tree: ", i, "number of children: ", best_path["children"][i])
    print("Cost value: ", cost[i])
    print("Cumulative Reward: ", best_path["value"][i])
    print("Average Reward: ", best_path["value"][i]/best_path["visits"][i], "\n")

Node at depth tree:  0 number of children:  4
Cost value:  -0.04207897977473342
Cumulative Reward:  609.8133938000806
Average Reward:  0.6092041896104701 

Node at depth tree:  1 number of children:  4
Cost value:  -0.1564470561095942
Cumulative Reward:  608.5627433969839
Average Reward:  0.6267381497394273 

Node at depth tree:  2 number of children:  4
Cost value:  -0.4151551721447462
Cumulative Reward:  602.864895147351
Average Reward:  0.6468507458662565 

Node at depth tree:  3 number of children:  4
Cost value:  -0.4151551721447463
Cumulative Reward:  593.5229666056723
Average Reward:  0.6602035223644853 

Node at depth tree:  4 number of children:  4
Cost value:  -0.4316265317187301
Cumulative Reward:  589.1112120305671
Average Reward:  0.6679265442523437 

Node at depth tree:  5 number of children:  4
Cost value:  -0.6241207277429219
Cumulative Reward:  583.8125015767978
Average Reward:  0.6741483851926071 

Node at depth tree:  6 number of children:  4
Cost value:  -0.62412072

At this poit we selct the ansatz as the best quantum circuit found in the path.

In [26]:
ansatz = quantum_circuit_path[cost.index(min(cost))]
print("Selected Ansatz: \n", ansatz)

Selected Ansatz: 
       ┌────────────┐                                                
v_0: ─┤ Ry(3.2947) ├────────────────────────────────────────────────
      ├────────────┤                                                
v_1: ─┤ Rx(3.3555) ├────────────────────────────────────────────────
     ┌┴────────────┤┌─────────────┐┌────────────┐     ┌────────────┐
v_2: ┤ Rz(0.72364) ├┤ Rz(0.71844) ├┤ Rz(5.8568) ├──■──┤ Rz(2.4268) ├
     └┬────────────┤└┬────────────┤└────────────┘┌─┴─┐└────────────┘
v_3: ─┤ Rz(1.2115) ├─┤ Rz(2.7083) ├──────────────┤ X ├──────────────
      └────────────┘ └────────────┘              └───┘              


## Parameter Optimization
Finally we optimize the parameters through a classical optimizer according to the objective function to minimize

In [27]:
problem(quantum_circuit=ansatz, gradient=True)

Step = 0,  Energy = -1.10810171 Ha
Step = 2,  Energy = -1.11004769 Ha
Step = 4,  Energy = -1.11174093 Ha
Step = 6,  Energy = -1.11317976 Ha
Step = 8,  Energy = -1.11436747 Ha
Step = 10,  Energy = -1.11531337 Ha
Step = 12,  Energy = -1.11603353 Ha
Step = 14,  Energy = -1.11655111 Ha
Step = 16,  Energy = -1.11689576 Ha
Step = 18,  Energy = -1.11710179 Ha
Step = 20,  Energy = -1.11720531 Ha
Step = 22,  Energy = -1.11724076 Ha
Step = 24,  Energy = -1.11723777 Ha
Step = 26,  Energy = -1.11721912 Ha
Step = 28,  Energy = -1.11720006 Ha
Step = 30,  Energy = -1.11718895 Ha
Step = 32,  Energy = -1.11718867 Ha
Step = 34,  Energy = -1.11719835 Ha
Step = 36,  Energy = -1.11721508 Ha
Step = 38,  Energy = -1.11723537 Ha
Step = 40,  Energy = -1.11725617 Ha
Step = 42,  Energy = -1.11727539 Ha
Step = 44,  Energy = -1.11729200 Ha
Step = 46,  Energy = -1.11730580 Ha
Step = 48,  Energy = -1.11731703 Ha
Step = 50,  Energy = -1.11732606 Ha
Step = 52,  Energy = -1.11733316 Ha
Step = 54,  Energy = -1.11733847 

[array(-1.10703555),
 array(-1.10810171),
 array(-1.10910602),
 array(-1.11004769),
 array(-1.11092611),
 array(-1.11174093),
 array(-1.11249207),
 array(-1.11317976),
 array(-1.11380457),
 array(-1.11436747),
 array(-1.11486981),
 array(-1.11531337),
 array(-1.11570038),
 array(-1.11603353),
 array(-1.11631593),
 array(-1.11655111),
 array(-1.11674299),
 array(-1.11689576),
 array(-1.11701385),
 array(-1.11710179),
 array(-1.11716413),
 array(-1.11720531),
 array(-1.11722954),
 array(-1.11724076),
 array(-1.11724247),
 array(-1.11723777),
 array(-1.11722928),
 array(-1.11721912),
 array(-1.11720897),
 array(-1.11720006),
 array(-1.11719322),
 array(-1.11718895),
 array(-1.11718745),
 array(-1.11718867),
 array(-1.11719242),
 array(-1.11719835),
 array(-1.11720605),
 array(-1.11721508),
 array(-1.11722499),
 array(-1.11723537),
 array(-1.11724586),
 array(-1.11725617),
 array(-1.11726606),
 array(-1.11727539),
 array(-1.11728405),
 array(-1.117292),
 array(-1.11729924),
 array(-1.11730